In [4]:
from fastai.vision.all import *

model_paths = [
    'resnet50',
    'efficientnet_b3',
    'densenet121',
    'resnet34',
    'mobilenetv3_large_100',
    'mobilenetv3_large_100_v2',
    'mobilenetv3_large_100_v3',
    'efficientnet_b0',
    'resnet50d',                     
    'mobilenetv3_large_100',         
    'densenet121',                 
    'regnety_040',                 
    'ghostnet_100',                
    'maxvit_tiny_rw_224',            
    'efficientformerv2_s0',          
]

learners = {}

for model_path in model_paths:

    full_path = f"../model/{model_path}/model.pkl"
    learn = load_learner(full_path)
    learners[model_path] = learn


learners

/opt/anaconda3/lib/python3.10/site-packages/fastai/learner.py:455: UserWarning: load_learner` uses Python's insecure pickle module, which can execute malicious arbitrary code when loading. Only load files you trust.
If you only need to load model weights and optimizer state, use the safe `Learner.load` instead.
  warn("load_learner` uses Python's insecure pickle module, which can execute malicious arbitrary code when loading. Only load files you trust.\nIf you only need to load model weights and optimizer state, use the safe `Learner.load` instead.")


{'resnet50': <fastai.learner.Learner at 0x33a2a1330>,
 'efficientnet_b3': <fastai.learner.Learner at 0x33a3af4c0>,
 'densenet121': <fastai.learner.Learner at 0x3400a7580>,
 'resnet34': <fastai.learner.Learner at 0x33c4af550>,
 'mobilenetv3_large_100': <fastai.learner.Learner at 0x33c555ba0>,
 'mobilenetv3_large_100_v2': <fastai.learner.Learner at 0x33c24bca0>,
 'mobilenetv3_large_100_v3': <fastai.learner.Learner at 0x33c4dfa30>,
 'efficientnet_b0': <fastai.learner.Learner at 0x33c557a30>,
 'resnet50d': <fastai.learner.Learner at 0x33fe537f0>,
 'regnety_040': <fastai.learner.Learner at 0x341def520>,
 'ghostnet_100': <fastai.learner.Learner at 0x33fd33820>,
 'maxvit_tiny_rw_224': <fastai.learner.Learner at 0x33c5e3820>,
 'efficientformerv2_s0': <fastai.learner.Learner at 0x342787970>}

In [5]:
import json

# Load JSON from file
with open('../model/ensemble_weights.json', 'r') as f:
    model_weights = json.load(f)

model_weights

{'mobilenetv3_large_100': 0.09924083115873755,
 'mobilenetv3_large_100_v2': 0.09924083115873755,
 'mobilenetv3_large_100_v3': 0.09924083115873755,
 'efficientnet_b3': 0.09637499217291971,
 'efficientnet_b0': 0.09499330977830908,
 'ghostnet_100': 0.09462535008094078,
 'resnet34': 0.09165850944645237,
 'resnet50d': 0.09154353324134662,
 'resnet50': 0.09102429628793353,
 'efficientformerv2_s0': 0.09018253177783798,
 'maxvit_tiny_rw_224': 0.08586070559809701,
 'densenet121': 0.08406226393836493,
 'regnety_040': 0.08043367651906061}

In [6]:
class LeanAIEnsembleModel:
    def __init__(self, learners: dict, model_weights: dict):
        """
        learners: dict of {model_name: Learner}
        model_weights: dict of {model_name: float}
        """
        self.learners = learners
        self.model_weights = model_weights

    def predict(self, image_path: str) -> float:
        raw_preds = self.predict_raw(image_path)  # dict: {model_name: prediction}
        
        total_weight = 0.0
        weighted_sum = 0.0

        for model_name, pred in raw_preds.items():
            weight = self.model_weights.get(model_name, 0.0)
            weighted_sum += pred * weight
            total_weight += weight

        if total_weight == 0:
            raise ValueError(f"No valid weights for prediction on '{image_path}'.")

        return weighted_sum / total_weight

    def predict_raw(self, image_path: str) -> dict:
        """
        Return a dict of raw model predictions for the input image.
        e.g., {'resnet50': 14.2, 'efficientnet_b0': 15.1, ...}
        """
        preds = {}
        img = PILImage.create(image_path)

        for model_name, learner in self.learners.items():
            try:
                _, _, output = learner.predict(img)
                preds[model_name] = float(output[0])
            except Exception as e:
                print(f"[Warning] Prediction failed for {model_name}: {e}")
                continue

        return preds


In [7]:
ensemble_model = LeanAIEnsembleModel(learners, model_weights)

In [8]:
ensemble_model.predict('../images/0_image_1.jpg')

9.15321514381041

In [25]:
import pandas as pd
from tqdm.notebook import tqdm

valid_df = pd.read_csv("../data/valid_set.csv")
preds = {}

for idx, row in tqdm(list(valid_df.iterrows()), total=len(valid_df)):
    try: 
        pred = ensemble_model.predict('../images/'+row['filename'])
        preds[row['filename']] = (pred)
    except Exception as e:
        print(e)
        continue

print(preds)

  0%|          | 0/316 [00:00<?, ?it/s]

[Errno 2] No such file or directory: '/Users/kalanjarvis-loewen/Desktop/Coding/learning/ml/LeanAI/core/images/347_image_1.jpg'


[Errno 2] No such file or directory: '/Users/kalanjarvis-loewen/Desktop/Coding/learning/ml/LeanAI/core/images/279_image_1.jpeg'


{'631_image_1.jpg': 12.501217823139525, '395_image_1.png': 15.198216053615136, '598_image_1.jpeg': 13.54678276166004, '258_image_3.jpg': 17.016488940348015, '248_image_1.jpg': 10.916066915640751, '767_image_1.png': 13.848089933663264, '251_image_1.jpg': 16.080522329600765, '133_image_1.jpeg': 14.216424351277325, '241_image_1.jpg': 12.641082270606296, '32_image_3.jpg': 12.128349662964343, '327_image_1.jpg': 8.863081453550652, '501_image_1.png': 14.448481041047982, '378_image_3.jpg': 15.18987794090472, '665_image_1.jpg': 18.099897247139882, '324_image_3.jpg': 13.40459377229636, '175_image_1.jpg': 15.723274106444633, '693_image_1.jpg': 11.454618241521903, '14_image_2.jpg': 20.619272710562417, '15_image_1.jpg': 11.45851930995186, '775_image_4.jpg': 24.542404206661214, '787_image_1.jpg': 16.4730667786977, '255_image_2.jpg': 15.08794227729639, '322_image_4.jpg': 15.176152606777183, '589_image_2.jpg': 11.523185617895038, '401_image_1.jpg': 12.69387034968609, '524_image_1.jpg': 10.163781383637

In [14]:
from sklearn.metrics import mean_absolute_error

y_true = []
y_pred = []

filenames = valid_df['filename'].tolist()

for fname in filenames:
    if fname in preds:
        y_true.append(valid_df.loc[valid_df['filename'] == fname, "target"].values[0])
        y_pred.append(preds[fname])


mae = mean_absolute_error(y_true, y_pred)
print(f"Model MAE: {mae}")

Model MAE: 2.00622032060318


In [9]:
# Lets make a pytorch ensemble now 

import torch
import torch.nn as nn

class TorchEnsembleModel(nn.Module):
    def __init__(self, models: list[nn.Module], weights: list[float]):
        super().__init__()
        assert len(models) == len(weights), "Number of models must match number of weights"
        self.models = nn.ModuleList(models)
        self.register_buffer("weights", torch.tensor(weights, dtype=torch.float32))

    def forward(self, x):
        outputs = [model(x) for model in self.models]
        outputs = torch.stack(outputs)  # shape: (num_models, batch_size, output_dim)
        weighted = (outputs * self.weights.view(-1, 1, 1)).sum(dim=0) / self.weights.sum()
        return weighted


In [11]:
learners.items()

dict_items([('resnet50', <fastai.learner.Learner object at 0x33a2a1330>), ('efficientnet_b3', <fastai.learner.Learner object at 0x33a3af4c0>), ('densenet121', <fastai.learner.Learner object at 0x3400a7580>), ('resnet34', <fastai.learner.Learner object at 0x33c4af550>), ('mobilenetv3_large_100', <fastai.learner.Learner object at 0x33c555ba0>), ('mobilenetv3_large_100_v2', <fastai.learner.Learner object at 0x33c24bca0>), ('mobilenetv3_large_100_v3', <fastai.learner.Learner object at 0x33c4dfa30>), ('efficientnet_b0', <fastai.learner.Learner object at 0x33c557a30>), ('resnet50d', <fastai.learner.Learner object at 0x33fe537f0>), ('regnety_040', <fastai.learner.Learner object at 0x341def520>), ('ghostnet_100', <fastai.learner.Learner object at 0x33fd33820>), ('maxvit_tiny_rw_224', <fastai.learner.Learner object at 0x33c5e3820>), ('efficientformerv2_s0', <fastai.learner.Learner object at 0x342787970>)])

In [17]:
models = [learner.model for learner in learners.values()]
weights = [weight for weight in model_weights.values()]

torch_ensemble = TorchEnsembleModel(models, weights)

In [39]:
from torchvision import transforms

def torch_ensemble_predict(image_path: str, ensemble_model, device='cpu'):

    transform = transforms.Compose([
        transforms.Resize((224, 224)),
        transforms.ToTensor(),
    ])

    # Load image
    img = Image.open(image_path).convert('RGB')

    # Apply transforms and add batch dimension
    input_tensor = transform(img).unsqueeze(0).to(device)

    with torch.no_grad():
        pred = torch_ensemble(input_tensor)

    return pred.cpu()

In [40]:
torch_ensemble_predict('../images/0_image_1.jpg', torch_ensemble)

tensor([[9.9604]])

In [50]:
import pandas as pd
from tqdm.notebook import tqdm

valid_df = pd.read_csv("../data/valid_set.csv")
preds = {}

for idx, row in tqdm(list(valid_df.iterrows()), total=len(valid_df)):
    try: 
        pred = torch_ensemble_predict('../images/'+row['filename'], ensemble_model)
        preds[row['filename']] = pred[0]
    except Exception as e:
        print(e)
        continue

print(preds)

  0%|          | 0/316 [00:00<?, ?it/s]

[Errno 2] No such file or directory: '/Users/kalanjarvis-loewen/Desktop/Coding/learning/ml/LeanAI/core/images/347_image_1.jpg'
[Errno 2] No such file or directory: '/Users/kalanjarvis-loewen/Desktop/Coding/learning/ml/LeanAI/core/images/279_image_1.jpeg'
{'631_image_1.jpg': tensor([11.8290]), '395_image_1.png': tensor([15.2334]), '598_image_1.jpeg': tensor([13.2494]), '258_image_3.jpg': tensor([16.6172]), '248_image_1.jpg': tensor([11.3338]), '767_image_1.png': tensor([14.5696]), '251_image_1.jpg': tensor([15.9641]), '133_image_1.jpeg': tensor([14.0504]), '241_image_1.jpg': tensor([12.1596]), '32_image_3.jpg': tensor([11.7733]), '327_image_1.jpg': tensor([9.0869]), '501_image_1.png': tensor([13.2706]), '378_image_3.jpg': tensor([15.0050]), '665_image_1.jpg': tensor([18.3191]), '324_image_3.jpg': tensor([13.5093]), '175_image_1.jpg': tensor([15.8700]), '693_image_1.jpg': tensor([11.5779]), '14_image_2.jpg': tensor([21.1209]), '15_image_1.jpg': tensor([11.5043]), '775_image_4.jpg': tenso

In [51]:
from sklearn.metrics import mean_absolute_error

y_true = []
y_pred = []



filenames = valid_df['filename'].tolist()

for fname in filenames:
    if fname in preds:
        y_true.append(valid_df.loc[valid_df['filename'] == fname, "target"].values[0])
        y_pred.append(preds[fname])


mae = mean_absolute_error(y_true, y_pred)
print(f"Model MAE: {mae}")

Model MAE: 2.0480791293587655


In [52]:
ensemble_model.eval()

AttributeError: 'LeanAIEnsembleModel' object has no attribute 'eval'

In [53]:
example_input = torch.randn(16, 3, 224, 224) 
traced_model = torch.jit.trace(ensemble_model, example_input)

RuntimeError: Could not get name of python class object